In [1]:
import pygame
import random
import time

# Inicialização do Pygame
pygame.init()

# Variáveis
simulation_speed = 1  # Velocidade inicial de 0.5 segundos
initial_rabbit_count = 10  # Quantidade inicial de coelhos
initial_plant_count = 100  # Quantidade inicial de plantas
plant_generation_rate = 20  # Quantidade de plantas geradas por época

SCREEN_WIDTH, SCREEN_HEIGHT = 1920, 1200  # Definir o tamanho da tela

# Cores
WHITE = (255, 255, 255)
BLACK = (0, 0, 0)
GREEN = (0, 255, 0)
BROWN = (165, 42, 42)
BLUE = (0, 0, 255)

# Definir o tamanho da grid e o tamanho da célula
GRID_SIZE_METERS = 40  # 40 metros (lado)
CELL_SIZE = 20  # Cada célula será 20x20 pixels
GRID_SIZE = GRID_SIZE_METERS * CELL_SIZE  # Tamanho total da grid em pixels

# Calcular a posição para centralizar a grid
GRID_X = (SCREEN_WIDTH - GRID_SIZE) // 2
GRID_Y = (SCREEN_HEIGHT - GRID_SIZE) // 2

# Criar a janela
screen = pygame.display.set_mode((SCREEN_WIDTH, SCREEN_HEIGHT))
pygame.display.set_caption("Grid Centralizada")

# Classe Plant
class Plant:
    def __init__(self, x, y):
        self.x = x
        self.y = y

# Classe Rabbit
class Rabbit:
    def __init__(self, x, y):
        self.x = x
        self.y = y
        self.lifespan = 10  # Vida do coelho em ciclos (20 ciclos)
        self.age = 0  # Idade do coelho
        self.is_baby = True  # Indica se o coelho é recém-nascido
    
    def move(self):
        direction = random.choice(['up', 'down', 'left', 'right'])
        if direction == 'up' and self.y > 0:
            self.y -= 1
        elif direction == 'down' and self.y < GRID_SIZE_METERS - 1:
            self.y += 1
        elif direction == 'left' and self.x > 0:
            self.x -= 1
        elif direction == 'right' and self.x < GRID_SIZE_METERS - 1:
            self.x += 1

    def eat_plants_and_reproduce(self, grid, rabbits):
        cell = grid[self.x][self.y]
        if cell.has_plant():
            # Remove the plant from the cell
            cell.remove_entity(Plant)
            self.reproduce(grid, rabbits)
            print(f"Coelho em ({self.x}, {self.y}) comeu planta")



    def reproduce(self, grid, rabbits):
        directions = [(-1, -1), (-1, 0), (-1, 1), (0, -1), (0, 1), (1, -1), (1, 0), (1, 1)]
        available_positions = [(self.x + dx, self.y + dy) for dx, dy in directions
            if 0 <= self.x + dx < GRID_SIZE_METERS and 0 <= self.y + dy < GRID_SIZE_METERS]

        available_positions = [pos for pos in available_positions if not grid[pos[0]][pos[1]].has_rabbit()]

        if available_positions:
            new_x, new_y = random.choice(available_positions)
            new_rabbit = Rabbit(new_x, new_y)
            rabbits.append(new_rabbit)
            grid[new_x][new_y].add_entity(new_rabbit)

    def age_rabbit(self):
        self.age += 1
        return self.age < self.lifespan

class GridCell:
    def __init__(self):
        self.entities = []

    def add_entity(self, entity):
        self.entities.append(entity)

    def remove_entity(self, entity_type):
        self.entities = [entity for entity in self.entities if not isinstance(entity, entity_type)]

    def has_rabbit(self):
        return any(isinstance(entity, Rabbit) for entity in self.entities)

    def has_plant(self):
        return any(isinstance(entity, Plant) for entity in self.entities)

    def get_entity_type(self):
        # Return 2 for rabbit, 1 for plant, 0 for empty
        if self.has_rabbit():
            return 2
        elif self.has_plant():
            return 1
        else:
            return 0

    def clear(self):
        self.entities.clear()


# Funções de desenho
def generate_plants(num_plants, grid):
    plants = []
    available_positions = [(x, y) for x in range(GRID_SIZE_METERS) for y in range(GRID_SIZE_METERS)
            if not grid[x][y].entities]

    num_plants = min(num_plants, len(available_positions))

    for _ in range(num_plants):
        x, y = random.choice(available_positions)
        plant = Plant(x, y)
        plants.append(plant)
        grid[x][y].add_entity(plant)
        available_positions.remove((x, y))

    return plants

def draw_grid(grid):
    for row in range(GRID_SIZE_METERS):
        for col in range(GRID_SIZE_METERS):
            rect = pygame.Rect(GRID_X + col * CELL_SIZE, GRID_Y + row * CELL_SIZE, CELL_SIZE, CELL_SIZE)
            
            # Determine the color based on the contents of the cell
            if grid[row][col].has_rabbit():
                color = BROWN if not grid[row][col].entities[0].is_baby else BLUE  # Adult or baby rabbit
            elif grid[row][col].has_plant():
                color = GREEN  # Plant
            else:
                color = WHITE  # Empty
            
            # Fill the rectangle with the appropriate color
            pygame.draw.rect(screen, color, rect)

            # Draw the cell border (for grid visibility)
            pygame.draw.rect(screen, BLACK, rect, 1)

def update_grid(grid, plants, rabbits):
    # Clear the grid first
    for row in grid:
        for cell in row:
            cell.clear()

    # Add plants to the grid first
    for plant in plants:
        grid[plant.x][plant.y].add_entity(plant)
    
    # Then add rabbits to ensure they are prioritized visually
    for rabbit in rabbits:
        grid[rabbit.x][rabbit.y].add_entity(rabbit)



def draw_rabbits(rabbits):
    for rabbit in rabbits:
        color = BLUE if rabbit.is_baby else BROWN
        rect = pygame.Rect(GRID_X + rabbit.x * CELL_SIZE, GRID_Y + rabbit.y * CELL_SIZE, CELL_SIZE, CELL_SIZE)
        pygame.draw.rect(screen, color, rect)

def draw_plants(plants):
    for plant in plants:
        rect = pygame.Rect(GRID_X + plant.x * CELL_SIZE, GRID_Y + plant.y * CELL_SIZE, CELL_SIZE, CELL_SIZE)
        pygame.draw.rect(screen, GREEN, rect)

def draw_button(text, x, y, width, height, active):
    color = BLACK if active else WHITE
    pygame.draw.rect(screen, color, (x, y, width, height), 0)
    pygame.draw.rect(screen, BLACK, (x, y, width, height), 3)
    font = pygame.font.SysFont(None, 48)
    text_surface = font.render(text, True, BLACK)
    screen.blit(text_surface, (x + (width - text_surface.get_width()) // 2, y + (height - text_surface.get_height()) // 2))

def draw_cell_numbers(grid):
    font = pygame.font.SysFont(None, 24)
    for row in range(GRID_SIZE_METERS):
        for col in range(GRID_SIZE_METERS):
            rect_x = GRID_X + col * CELL_SIZE
            rect_y = GRID_Y + row * CELL_SIZE
            cell = grid[row][col]

            # Get the entity type (2 for rabbit, 1 for plant, 0 for empty)
            number = cell.get_entity_type()

            # Draw the number in the cell
            text_surface = font.render(str(number), True, BLACK)
            screen.blit(text_surface, (rect_x + CELL_SIZE // 2 - text_surface.get_width() // 2, 
                                       rect_y + CELL_SIZE // 2 - text_surface.get_height() // 2))



def draw_legend():
    font = pygame.font.SysFont(None, 36)
    legend_x = GRID_X + GRID_SIZE + 20
    legend_y = GRID_Y

    legend_text = ["Legend:", "0: Empty", "1: Plant", "2: Rabbit"]
    for i, text in enumerate(legend_text):
        text_surface = font.render(text, True, BLACK)
        screen.blit(text_surface, (legend_x, legend_y + i * 30))


def main():
    clock = pygame.time.Clock()
    running = True
    show_grid = False
    plants = []  # List of plants
    rabbits = []
    
    grid = [[GridCell() for _ in range(GRID_SIZE_METERS)] for _ in range(GRID_SIZE_METERS)]

    button_rect = pygame.Rect(SCREEN_WIDTH // 2 - 100, SCREEN_HEIGHT // 2 - 50, 200, 100)  # Start button in the center
    simulation_started = False  # Check if the simulation has started

    last_plant_time = time.time()
    last_rabbit_move = time.time()

    while running:
        # Clear screen with a white background
        screen.fill(WHITE)

        # Event handling
        for event in pygame.event.get():
            if event.type == pygame.QUIT:
                running = False
            if event.type == pygame.MOUSEBUTTONDOWN:
                if not simulation_started and button_rect.collidepoint(event.pos):
                    # Start simulation
                    show_grid = True
                    simulation_started = True
                    plants = generate_plants(initial_plant_count, grid)  # Generate initial plants

                    # Generate initial rabbits
                    for _ in range(initial_rabbit_count):
                        while True:
                            x, y = random.randint(0, GRID_SIZE_METERS - 1), random.randint(0, GRID_SIZE_METERS - 1)
                            if not grid[x][y].has_rabbit():
                                rabbit = Rabbit(x, y)
                                rabbits.append(rabbit)
                                grid[x][y].add_entity(rabbit)
                                break

        # If simulation is started, update and draw the grid
        if show_grid:
            # Update grid state (clear previous entities, add current ones)
            update_grid(grid, plants, rabbits)

            # Generate new plants based on simulation speed
            if time.time() - last_plant_time >= simulation_speed:
                new_plants = generate_plants(plant_generation_rate, grid)
                plants.extend(new_plants)
                last_plant_time = time.time()

            # Move rabbits and let them eat plants or reproduce
            if time.time() - last_rabbit_move >= simulation_speed:
                for rabbit in rabbits[:]:  # Copy list to avoid modification during iteration
                    rabbit.move()
                    rabbit.eat_plants_and_reproduce(grid, rabbits)
                    rabbit.is_baby = rabbit.age < 1
                    if not rabbit.age_rabbit():
                        rabbits.remove(rabbit)
                last_rabbit_move = time.time()

            # Draw the updated grid and entities
            draw_grid()
            draw_plants(plants)
            draw_rabbits(rabbits)
            draw_cell_numbers(grid)
            draw_legend()
        else:
            # Draw the Start button if the simulation hasn't started yet
            draw_button("Start", button_rect.x, button_rect.y, button_rect.width, button_rect.height, True)

        # Update display
        pygame.display.flip()
        clock.tick(60)  # Cap the frame rate to 60 FPS

    # Quit Pygame
    pygame.quit()

# Run the simulation
main()



pygame 2.6.1 (SDL 2.28.4, Python 3.11.9)
Hello from the pygame community. https://www.pygame.org/contribute.html


KeyboardInterrupt: 

In [ ]:
import pygame
import random
import time

# Inicialização do Pygame
pygame.init()

# Variáveis
simulation_speed = 1  # Velocidade inicial de 0.5 segundos
initial_rabbit_count = 10  # Quantidade inicial de coelhos
initial_plant_count = 100  # Quantidade inicial de plantas
plant_generation_rate = 20  # Quantidade de plantas geradas por época

SCREEN_WIDTH, SCREEN_HEIGHT = 1920, 1200  # Definir o tamanho da tela

# Cores
WHITE = (255, 255, 255)
BLACK = (0, 0, 0)
GREEN = (0, 255, 0)
BROWN = (165, 42, 42)
BLUE = (0, 0, 255)

# Definir o tamanho da grid e o tamanho da célula
GRID_SIZE_METERS = 40  # 40 metros (lado)
CELL_SIZE = 20  # Cada célula será 20x20 pixels
GRID_SIZE = GRID_SIZE_METERS * CELL_SIZE  # Tamanho total da grid em pixels

# Calcular a posição para centralizar a grid
GRID_X = (SCREEN_WIDTH - GRID_SIZE) // 2
GRID_Y = (SCREEN_HEIGHT - GRID_SIZE) // 2

# Criar a janela
screen = pygame.display.set_mode((SCREEN_WIDTH, SCREEN_HEIGHT))
pygame.display.set_caption("Grid Centralizada")

# Classe Plant
class Plant:
    def __init__(self, x, y):
        self.x = x
        self.y = y

# Classe Rabbit
class Rabbit:
    def __init__(self, x, y):
        self.x = x
        self.y = y
        self.lifespan = 10  # Vida do coelho em ciclos (20 ciclos)
        self.age = 0  # Idade do coelho
        self.is_baby = True  # Indica se o coelho é recém-nascido
    
    def move(self):
        direction = random.choice(['up', 'down', 'left', 'right'])
        if direction == 'up' and self.y > 0:
            self.y -= 1
        elif direction == 'down' and self.y < GRID_SIZE_METERS - 1:
            self.y += 1
        elif direction == 'left' and self.x > 0:
            self.x -= 1
        elif direction == 'right' and self.x < GRID_SIZE_METERS - 1:
            self.x += 1
        print(f"Rabbit moved to ({self.x}, {self.y})")  # Debugging

    def eat_plants_and_reproduce(self, grid, rabbits):
        cell = grid[self.x][self.y]
        if cell.has_plant():
            # Remove the plant from the cell
            cell.remove_entity(Plant)
            self.reproduce(grid, rabbits)
            print(f"Coelho em ({self.x}, {self.y}) comeu planta")  # Debugging

    def reproduce(self, grid, rabbits):
        directions = [(-1, -1), (-1, 0), (-1, 1), (0, -1), (0, 1), (1, -1), (1, 0), (1, 1)]
        available_positions = [(self.x + dx, self.y + dy) for dx, dy in directions
            if 0 <= self.x + dx < GRID_SIZE_METERS and 0 <= self.y + dy < GRID_SIZE_METERS]

        available_positions = [pos for pos in available_positions if not grid[pos[0]][pos[1]].has_rabbit()]

        if available_positions:
            new_x, new_y = random.choice(available_positions)
            new_rabbit = Rabbit(new_x, new_y)
            rabbits.append(new_rabbit)
            grid[new_x][new_y].add_entity(new_rabbit)

    def age_rabbit(self):
        self.age += 1
        return self.age < self.lifespan

class GridCell:
    def __init__(self):
        self.entities = []

    def add_entity(self, entity):
        self.entities.append(entity)

    def remove_entity(self, entity_type):
        self.entities = [entity for entity in self.entities if not isinstance(entity, entity_type)]

    def has_rabbit(self):
        return any(isinstance(entity, Rabbit) for entity in self.entities)

    def has_plant(self):
        return any(isinstance(entity, Plant) for entity in self.entities)

    def get_entity_type(self):
        # Return 2 for rabbit, 1 for plant, 0 for empty
        if self.has_rabbit():
            return 2
        elif self.has_plant():
            return 1
        else:
            return 0

    def clear(self):
        self.entities.clear()

    def debug_print(self):
        if self.has_rabbit():
            return "Rabbit"
        elif self.has_plant():
            return "Plant"
        else:
            return "Empty"

# Debugging function to print the grid state
def print_grid_state(grid):
    print("\nGrid State:")
    for row in range(GRID_SIZE_METERS):
        for col in range(GRID_SIZE_METERS):
            cell_status = grid[row][col].debug_print()
            print(f"({row}, {col}): {cell_status}", end=" | ")
        print()  # Newline for each row

# Funções de desenho
def generate_plants(num_plants, grid):
    plants = []
    available_positions = [(x, y) for x in range(GRID_SIZE_METERS) for y in range(GRID_SIZE_METERS)
            if not grid[x][y].entities]

    num_plants = min(num_plants, len(available_positions))

    for _ in range(num_plants):
        x, y = random.choice(available_positions)
        plant = Plant(x, y)
        plants.append(plant)
        grid[x][y].add_entity(plant)
        available_positions.remove((x, y))

    return plants


def draw_rabbits(rabbits):
    for rabbit in rabbits:
        color = BLUE if rabbit.is_baby else BROWN
        rect = pygame.Rect(GRID_X + rabbit.x * CELL_SIZE, GRID_Y + rabbit.y * CELL_SIZE, CELL_SIZE, CELL_SIZE)
        pygame.draw.rect(screen, color, rect)

def draw_plants(plants):
    for plant in plants:
        rect = pygame.Rect(GRID_X + plant.x * CELL_SIZE, GRID_Y + plant.y * CELL_SIZE, CELL_SIZE, CELL_SIZE)
        pygame.draw.rect(screen, GREEN, rect)

def draw_button(text, x, y, width, height, active):
    color = BLACK if active else WHITE
    pygame.draw.rect(screen, color, (x, y, width, height), 0)
    pygame.draw.rect(screen, BLACK, (x, y, width, height), 3)
    font = pygame.font.SysFont(None, 48)
    text_surface = font.render(text, True, BLACK)
    screen.blit(text_surface, (x + (width - text_surface.get_width()) // 2, y + (height - text_surface.get_height()) // 2))

def draw_grid(grid):
    for row in range(GRID_SIZE_METERS):
        for col in range(GRID_SIZE_METERS):
            rect = pygame.Rect(GRID_X + col * CELL_SIZE, GRID_Y + row * CELL_SIZE, CELL_SIZE, CELL_SIZE)
            
            # Determine the color based on the contents of the cell
            if grid[row][col].has_rabbit():
                color = BROWN if not grid[row][col].entities[0].is_baby else BLUE  # Adult or baby rabbit
            elif grid[row][col].has_plant():
                color = GREEN  # Plant
            else:
                color = WHITE  # Empty
            
            # Fill the rectangle with the appropriate color
            pygame.draw.rect(screen, color, rect)

            # Draw the cell border (for grid visibility)
            pygame.draw.rect(screen, BLACK, rect, 1)

def update_grid(grid, plants, rabbits):
    # Clear the grid first
    for row in grid:
        for cell in row:
            cell.clear()

    # Add plants to the grid first
    for plant in plants:
        grid[plant.x][plant.y].add_entity(plant)
    
    # Then add rabbits to ensure they are prioritized visually
    for rabbit in rabbits:
        grid[rabbit.x][rabbit.y].add_entity(rabbit)



def draw_cell_numbers(grid):
    font = pygame.font.SysFont(None, 24)
    for row in range(GRID_SIZE_METERS):
        for col in range(GRID_SIZE_METERS):
            rect_x = GRID_X + col * CELL_SIZE
            rect_y = GRID_Y + row * CELL_SIZE
            cell = grid[row][col]

            # Get the entity type (2 for rabbit, 1 for plant, 0 for empty)
            number = cell.get_entity_type()

            # Draw the number in the cell
            text_surface = font.render(str(number), True, BLACK)
            screen.blit(text_surface, (rect_x + CELL_SIZE // 2 - text_surface.get_width() // 2, 
                                       rect_y + CELL_SIZE // 2 - text_surface.get_height() // 2))

def draw_legend():
    font = pygame.font.SysFont(None, 36)
    legend_x = GRID_X + GRID_SIZE + 20
    legend_y = GRID_Y

    legend_text = ["Legend:", "0: Empty", "1: Plant", "2: Rabbit"]
    for i, text in enumerate(legend_text):
        text_surface = font.render(text, True, BLACK)
        screen.blit(text_surface, (legend_x, legend_y + i * 30))


def main():
    clock = pygame.time.Clock()
    running = True
    show_grid = False
    plants = []  # List of plants
    rabbits = []
    
    grid = [[GridCell() for _ in range(GRID_SIZE_METERS)] for _ in range(GRID_SIZE_METERS)]

    button_rect = pygame.Rect(SCREEN_WIDTH // 2 - 100, SCREEN_HEIGHT // 2 - 50, 200, 100)  # Start button in the center
    simulation_started = False  # Check if the simulation has started

    last_plant_time = time.time()
    last_rabbit_move = time.time()

    while running:
        # Clear screen with a white background
        screen.fill(WHITE)

        # Event handling
        for event in pygame.event.get():
            if event.type == pygame.QUIT:
                running = False
            if event.type == pygame.MOUSEBUTTONDOWN:
                if not simulation_started and button_rect.collidepoint(event.pos):
                    # Start simulation
                    show_grid = True
                    simulation_started = True
                    plants = generate_plants(initial_plant_count, grid)  # Generate initial plants

                    # Generate initial rabbits
                    for _ in range(initial_rabbit_count):
                        while True:
                            x, y = random.randint(0, GRID_SIZE_METERS - 1), random.randint(0, GRID_SIZE_METERS - 1)
                            if not grid[x][y].has_rabbit():
                                rabbit = Rabbit(x, y)
                                rabbits.append(rabbit)
                                grid[x][y].add_entity(rabbit)
                                break

        # If simulation is started, update and draw the grid
        if show_grid:
            # Update grid state (clear previous entities, add current ones)
            update_grid(grid, plants, rabbits)

            # Generate new plants based on simulation speed
            if time.time() - last_plant_time >= simulation_speed:
                new_plants = generate_plants(plant_generation_rate, grid)
                plants.extend(new_plants)
                last_plant_time = time.time()

            # Move rabbits and let them eat plants or reproduce
            if time.time() - last_rabbit_move >= simulation_speed:
                for rabbit in rabbits[:]:  # Copy list to avoid modification during iteration
                    rabbit.move()
                    rabbit.eat_plants_and_reproduce(grid, rabbits)
                    rabbit.is_baby = rabbit.age < 1
                    if not rabbit.age_rabbit():
                        rabbits.remove(rabbit)
                last_rabbit_move = time.time()

            # Debug print the current grid state
            print_grid_state(grid)

            # Draw the updated grid and entities
            draw_grid()
            draw_plants(plants)
            draw_rabbits(rabbits)
            draw_cell_numbers(grid)
            draw_legend()
        else:
            # Draw the Start button if the simulation hasn't started yet
            draw_button("Start", button_rect.x, button_rect.y, button_rect.width, button_rect.height, True)

        # Update display
        pygame.display.flip()
        clock.tick(60)  # Cap the frame rate to 60 FPS

    # Quit Pygame
    pygame.quit()

# Run the simulation
main()



Grid State:
(0, 0): Empty | (0, 1): Empty | (0, 2): Empty | (0, 3): Empty | (0, 4): Empty | (0, 5): Empty | (0, 6): Empty | (0, 7): Empty | (0, 8): Empty | (0, 9): Empty | (0, 10): Empty | (0, 11): Empty | (0, 12): Empty | (0, 13): Empty | (0, 14): Empty | (0, 15): Empty | (0, 16): Empty | (0, 17): Empty | (0, 18): Empty | (0, 19): Empty | (0, 20): Empty | (0, 21): Empty | (0, 22): Empty | (0, 23): Empty | (0, 24): Plant | (0, 25): Empty | (0, 26): Empty | (0, 27): Empty | (0, 28): Plant | (0, 29): Empty | (0, 30): Plant | (0, 31): Empty | (0, 32): Empty | (0, 33): Empty | (0, 34): Empty | (0, 35): Empty | (0, 36): Empty | (0, 37): Empty | (0, 38): Plant | (0, 39): Empty | 
(1, 0): Empty | (1, 1): Empty | (1, 2): Empty | (1, 3): Empty | (1, 4): Empty | (1, 5): Empty | (1, 6): Empty | (1, 7): Empty | (1, 8): Empty | (1, 9): Empty | (1, 10): Empty | (1, 11): Plant | (1, 12): Empty | (1, 13): Plant | (1, 14): Empty | (1, 15): Empty | (1, 16): Empty | (1, 17): Empty | (1, 18): Empty | (1,

TypeError: draw_grid() missing 1 required positional argument: 'grid'

In [3]:
import pygame
import random
import time

# Inicialização do Pygame
pygame.init()

# Variáveis
simulation_speed = 0.1  # Velocidade inicial de 0.5 segundos
initial_rabbit_count = 10  # Quantidade inicial de coelhos
initial_plant_count = 100  # Quantidade inicial de plantas
plant_generation_rate = 20  # Quantidade de plantas geradas por época

SCREEN_WIDTH, SCREEN_HEIGHT = 1920, 1200  # Definir o tamanho da tela

# Cores
WHITE = (255, 255, 255)
BLACK = (0, 0, 0)
GREEN = (0, 255, 0)
BROWN = (165, 42, 42)
BLUE = (0, 0, 255)

# Definir o tamanho da grid e o tamanho da célula
GRID_SIZE_METERS = 40  # 40 metros (lado)
CELL_SIZE = 20  # Cada célula será 20x20 pixels
GRID_SIZE = GRID_SIZE_METERS * CELL_SIZE  # Tamanho total da grid em pixels

# Calcular a posição para centralizar a grid
GRID_X = (SCREEN_WIDTH - GRID_SIZE) // 2
GRID_Y = (SCREEN_HEIGHT - GRID_SIZE) // 2

# Criar a janela
screen = pygame.display.set_mode((SCREEN_WIDTH, SCREEN_HEIGHT))
pygame.display.set_caption("Grid Centralizada")

# Classe Plant
class Plant:
    def __init__(self, x, y):
        self.x = x
        self.y = y

# Classe Rabbit
class Rabbit:
    def __init__(self, x, y):
        self.x = x
        self.y = y
        self.lifespan = 5  # Vida do coelho em ciclos (20 ciclos)
        self.age = 0  # Idade do coelho
        self.is_baby = True  # Indica se o coelho é recém-nascido
    
    def move(self):
        direction = random.choice(['up', 'down', 'left', 'right'])
        if direction == 'up' and self.y > 0:
            self.y -= 1
        elif direction == 'down' and self.y < GRID_SIZE_METERS - 1:
            self.y += 1
        elif direction == 'left' and self.x > 0:
            self.x -= 1
        elif direction == 'right' and self.x < GRID_SIZE_METERS - 1:
            self.x += 1
        print(f"Rabbit moved to ({self.x}, {self.y})")  # Debugging

    def eat_plants_and_reproduce(self, grid, rabbits):
        cell = grid[self.x][self.y]
        if cell.has_plant():
            # Remove the plant from the cell
            cell.remove_entity(Plant)
            self.reproduce(grid, rabbits)
            print(f"Coelho em ({self.x}, {self.y}) comeu planta")  # Debugging

    def reproduce(self, grid, rabbits):
        directions = [(-1, -1), (-1, 0), (-1, 1), (0, -1), (0, 1), (1, -1), (1, 0), (1, 1)]
        available_positions = [(self.x + dx, self.y + dy) for dx, dy in directions
            if 0 <= self.x + dx < GRID_SIZE_METERS and 0 <= self.y + dy < GRID_SIZE_METERS]

        available_positions = [pos for pos in available_positions if not grid[pos[0]][pos[1]].has_rabbit()]

        if available_positions:
            new_x, new_y = random.choice(available_positions)
            new_rabbit = Rabbit(new_x, new_y)
            rabbits.append(new_rabbit)
            grid[new_x][new_y].add_entity(new_rabbit)

    def age_rabbit(self):
        self.age += 1
        return self.age < self.lifespan

class GridCell:
    def __init__(self):
        self.entities = []

    def add_entity(self, entity):
        self.entities.append(entity)

    def remove_entity(self, entity_type):
        self.entities = [entity for entity in self.entities if not isinstance(entity, entity_type)]

    def has_rabbit(self):
        return any(isinstance(entity, Rabbit) for entity in self.entities)

    def has_plant(self):
        return any(isinstance(entity, Plant) for entity in self.entities)

    def get_entity_type(self):
        # Return 2 for rabbit, 1 for plant, 0 for empty
        if self.has_rabbit():
            return 2
        elif self.has_plant():
            return 1
        else:
            return 0

    def clear(self):
        self.entities.clear()

    def debug_print(self):
        if self.has_rabbit():
            return "Rabbit"
        elif self.has_plant():
            return "Plant"
        else:
            return "Empty"

# Debugging function to print the grid state
def print_grid_state(grid):
    print("\nGrid State:")
    for row in range(GRID_SIZE_METERS):
        for col in range(GRID_SIZE_METERS):
            cell_status = grid[row][col].debug_print()
            print(f"({row}, {col}): {cell_status}", end=" | ")
        print()  # Newline for each row

# Funções de desenho
def generate_plants(num_plants, grid):
    plants = []
    available_positions = [(x, y) for x in range(GRID_SIZE_METERS) for y in range(GRID_SIZE_METERS)
            if not grid[x][y].entities]

    num_plants = min(num_plants, len(available_positions))

    for _ in range(num_plants):
        x, y = random.choice(available_positions)
        plant = Plant(x, y)
        plants.append(plant)
        grid[x][y].add_entity(plant)
        available_positions.remove((x, y))

    return plants

# Funções de desenho
def draw_grid(grid):
    for row in range(GRID_SIZE_METERS):
        for col in range(GRID_SIZE_METERS):
            rect = pygame.Rect(GRID_X + col * CELL_SIZE, GRID_Y + row * CELL_SIZE, CELL_SIZE, CELL_SIZE)

            # Determine the color based on the contents of the cell
            if grid[row][col].has_rabbit():
                # Get the first rabbit entity to check if it's a baby
                for entity in grid[row][col].entities:
                    if isinstance(entity, Rabbit):
                        color = BROWN if not entity.is_baby else BLUE  # Adult or baby rabbit
                        break
            elif grid[row][col].has_plant():
                color = GREEN  # Plant
            else:
                color = WHITE  # Empty
            
            # Fill the rectangle with the appropriate color
            pygame.draw.rect(screen, color, rect)

            # Draw the cell border (for grid visibility)
            pygame.draw.rect(screen, BLACK, rect, 1)

def draw_rabbits(rabbits):
    for rabbit in rabbits:
        color = BLUE if rabbit.is_baby else BROWN
        rect = pygame.Rect(GRID_X + rabbit.x * CELL_SIZE, GRID_Y + rabbit.y * CELL_SIZE, CELL_SIZE, CELL_SIZE)
        pygame.draw.rect(screen, color, rect)

def draw_plants(plants):
    for plant in plants:
        rect = pygame.Rect(GRID_X + plant.x * CELL_SIZE, GRID_Y + plant.y * CELL_SIZE, CELL_SIZE, CELL_SIZE)
        pygame.draw.rect(screen, GREEN, rect)

def draw_button(text, x, y, width, height, active):
    color = BLACK if active else WHITE
    pygame.draw.rect(screen, color, (x, y, width, height), 0)
    pygame.draw.rect(screen, BLACK, (x, y, width, height), 3)
    font = pygame.font.SysFont(None, 48)
    text_surface = font.render(text, True, WHITE)
    screen.blit(text_surface, (x + (width - text_surface.get_width()) // 2, y + (height - text_surface.get_height()) // 2))

def update_grid(grid, plants, rabbits):
    # Clear the grid first
    for row in grid:
        for cell in row:
            cell.clear()

    # Add plants to the grid first
    for plant in plants:
        grid[plant.x][plant.y].add_entity(plant)
    
    # Then add rabbits to ensure they are prioritized visually
    for rabbit in rabbits:
        grid[rabbit.x][rabbit.y].add_entity(rabbit)

def draw_cell_numbers(grid):
    font = pygame.font.SysFont(None, 24)
    for row in range(GRID_SIZE_METERS):
        for col in range(GRID_SIZE_METERS):
            rect_x = GRID_X + col * CELL_SIZE
            rect_y = GRID_Y + row * CELL_SIZE
            cell = grid[row][col]

            # Get the entity type (2 for rabbit, 1 for plant, 0 for empty)
            number = cell.get_entity_type()

            # Draw the number in the cell
            text_surface = font.render(str(number), True, BLACK)
            screen.blit(text_surface, (rect_x + CELL_SIZE // 2 - text_surface.get_width() // 2, 
                                       rect_y + CELL_SIZE // 2 - text_surface.get_height() // 2))

def draw_legend():
    font = pygame.font.SysFont(None, 36)
    legend_x = GRID_X + GRID_SIZE + 20
    legend_y = GRID_Y

    legend_text = ["Legend:", "0: Empty", "1: Plant", "2: Rabbit"]
    for i, text in enumerate(legend_text):
        text_surface = font.render(text, True, BLACK)
        screen.blit(text_surface, (legend_x, legend_y + i * 30))


def main():
    clock = pygame.time.Clock()
    running = True
    show_grid = False
    plants = []  # List of plants
    rabbits = []
    
    grid = [[GridCell() for _ in range(GRID_SIZE_METERS)] for _ in range(GRID_SIZE_METERS)]

    button_rect = pygame.Rect(SCREEN_WIDTH // 2 - 100, SCREEN_HEIGHT // 2 - 50, 200, 100)  # Start button in the center
    simulation_started = False  # Check if the simulation has started

    last_plant_time = time.time()
    last_rabbit_move = time.time()

    while running:
        # Clear screen with a white background
        screen.fill(WHITE)

        # Event handling
        for event in pygame.event.get():
            if event.type == pygame.QUIT:
                running = False
            if event.type == pygame.MOUSEBUTTONDOWN:
                if not simulation_started and button_rect.collidepoint(event.pos):
                    # Start simulation
                    show_grid = True
                    simulation_started = True
                    plants = generate_plants(initial_plant_count, grid)  # Generate initial plants

                    # Generate initial rabbits
                    for _ in range(initial_rabbit_count):
                        while True:
                            x, y = random.randint(0, GRID_SIZE_METERS - 1), random.randint(0, GRID_SIZE_METERS - 1)
                            if not grid[x][y].has_rabbit():
                                rabbit = Rabbit(x, y)
                                rabbits.append(rabbit)
                                grid[x][y].add_entity(rabbit)
                                break

        # If simulation is started, update and draw the grid
        if show_grid:
            # Update grid state (clear previous entities, add current ones)
            update_grid(grid, plants, rabbits)

            # Generate new plants based on simulation speed
            if time.time() - last_plant_time >= simulation_speed:
                new_plants = generate_plants(plant_generation_rate, grid)
                plants.extend(new_plants)
                last_plant_time = time.time()

            # Move rabbits and let them eat plants or reproduce
            if time.time() - last_rabbit_move >= simulation_speed:
                for rabbit in rabbits[:]:  # Copy list to avoid modification during iteration
                    rabbit.move()
                    rabbit.eat_plants_and_reproduce(grid, rabbits)
                    rabbit.is_baby = rabbit.age < 1
                    if not rabbit.age_rabbit():
                        rabbits.remove(rabbit)
                last_rabbit_move = time.time()

            # Debug print the current grid state
            print_grid_state(grid)

            # Draw the updated grid and entities
            draw_grid(grid)  # Pass the grid argument
            draw_cell_numbers(grid)
            draw_legend()
        else:
            # Draw the Start button if the simulation hasn't started yet
            draw_button("Start", button_rect.x, button_rect.y, button_rect.width, button_rect.height, True)

        # Update display
        pygame.display.flip()
        clock.tick(60)  # Cap the frame rate to 60 FPS

    # Quit Pygame
    pygame.quit()

# Run the simulation
main()


Rabbit moved to (15, 12)
Rabbit moved to (4, 7)
Rabbit moved to (7, 22)
Rabbit moved to (26, 34)
Rabbit moved to (3, 20)
Rabbit moved to (34, 23)
Rabbit moved to (31, 21)
Rabbit moved to (37, 14)
Rabbit moved to (11, 20)
Rabbit moved to (39, 27)

Grid State:
(0, 0): Empty | (0, 1): Plant | (0, 2): Empty | (0, 3): Empty | (0, 4): Plant | (0, 5): Empty | (0, 6): Empty | (0, 7): Empty | (0, 8): Empty | (0, 9): Empty | (0, 10): Plant | (0, 11): Empty | (0, 12): Empty | (0, 13): Empty | (0, 14): Empty | (0, 15): Plant | (0, 16): Empty | (0, 17): Empty | (0, 18): Empty | (0, 19): Empty | (0, 20): Empty | (0, 21): Empty | (0, 22): Empty | (0, 23): Empty | (0, 24): Empty | (0, 25): Empty | (0, 26): Empty | (0, 27): Empty | (0, 28): Empty | (0, 29): Empty | (0, 30): Empty | (0, 31): Empty | (0, 32): Plant | (0, 33): Empty | (0, 34): Empty | (0, 35): Empty | (0, 36): Empty | (0, 37): Empty | (0, 38): Empty | (0, 39): Empty | 
(1, 0): Empty | (1, 1): Empty | (1, 2): Empty | (1, 3): Empty | (1, 4)

AttributeError: 'GridCell' object has no attribute 'clear'